In [1]:
import torch
import pandas as pd
import numpy as np
from tqdm import tqdm
import matplotlib
import matplotlib.pyplot as plt
import seaborn as sns

In [2]:
matplotlib.rc('text', usetex=True)
matplotlib.rcParams['text.latex.preamble']=[r"\usepackage{amsmath}"]
sns.set_style("darkgrid")

C:\PROGRAMY\Anaconda3\envs\ium\lib\site-packages\ipykernel_launcher.py:2: MatplotlibDeprecationWarning: Support for setting an rcParam that expects a str value to a non-str value is deprecated since 3.5 and support will be removed two minor releases later.
  


In [3]:
train_dataset = pd.read_csv('../train_dataset.csv')
test_dataset = pd.read_csv('../test_dataset.csv')

In [5]:
X_train = train_dataset.drop(columns=['No-show']).to_numpy()
X_test = test_dataset.drop(columns=['No-show']).to_numpy()
y_train = train_dataset['No-show'].to_numpy()
y_test = test_dataset['No-show'].to_numpy()

In [7]:
class LogisticRegression(torch.nn.Module):
    def __init__(self, input_dim, output_dim):
        super(LogisticRegression, self).__init__()
        self.linear = torch.nn.Linear(input_dim, output_dim)     
    def forward(self, x):
        outputs = torch.sigmoid(self.linear(x))
        return outputs

In [8]:
epochs = 50_000
input_dim = 9
output_dim = 1
learning_rate = 0.01

In [9]:
model = LogisticRegression(input_dim, output_dim)

In [10]:
criterion = torch.nn.BCELoss()

In [11]:
optimizer = torch.optim.SGD(model.parameters(), lr=learning_rate)

In [12]:
X_train, X_test = torch.Tensor(X_train),torch.Tensor(X_test)
y_train, y_test = torch.Tensor(y_train),torch.Tensor(y_test)

In [13]:
losses = []
losses_test = []
Iterations = []
iter = 0
for epoch in tqdm(range(int(epochs)), desc='Training Epochs'):
    x = X_train
    labels = y_train
    optimizer.zero_grad() # Setting our stored gradients equal to zero
    outputs = model(X_train)
    loss = criterion(torch.squeeze(outputs), labels) 
    
    loss.backward() # Computes the gradient of the given tensor w.r.t. the weights/bias
    
    optimizer.step() # Updates weights and biases with the optimizer (SGD)
    
    iter+=1
    if iter%10000==0:
        with torch.no_grad():
            # Calculating the loss and accuracy for the test dataset
            correct_test = 0
            total_test = 0
            outputs_test = torch.squeeze(model(X_test))
            loss_test = criterion(outputs_test, y_test)
            
            predicted_test = outputs_test.round().detach().numpy()
            total_test += y_test.size(0)
            correct_test += np.sum(predicted_test == y_test.detach().numpy())
            accuracy_test = 100 * correct_test/total_test
            losses_test.append(loss_test.item())
            
            # Calculating the loss and accuracy for the train dataset
            total = 0
            correct = 0
            total += y_train.size(0)
            correct += np.sum(torch.squeeze(outputs).round().detach().numpy() == y_train.detach().numpy())
            accuracy = 100 * correct/total
            losses.append(loss.item())
            Iterations.append(iter)

Training Epochs: 100%|██████████| 50000/50000 [02:01<00:00, 411.29it/s]


In [14]:
print(f"Iteration: {iter}. \nTest - Loss: {loss_test.item()}. Accuracy: {accuracy_test}")
print(f"Train -  Loss: {loss.item()}. Accuracy: {accuracy}\n")

Iteration: 50000. 
Test - Loss: 0.480914831161499. Accuracy: 79.76567447751742
Train -  Loss: 0.48352959752082825. Accuracy: 79.37570685365301



In [15]:
with open("logs.txt", "a") as myfile:
    myfile.write(f"loss={loss.item()}, accuracy={accuracy}\n")